In [1]:
import setup_django
setup_django.init()

In [30]:
import pandas as pd
from django.conf import settings
from ratings.models import Rating
from movies.models import Movie
LINKS_SAMLL_CSV = settings.DATA_DIR / 'links_small.csv'
LINKS_SAMLL_CSV.exists()

True

In [5]:
qs = Rating.objects.all()
missing_movie_ids = []
for instance in qs:
    if instance.content_object is None:
        missing_movie_ids.append(instance.object_id)

In [10]:
total = len(missing_movie_ids) ## missing ratings at movies
total_missing = list(set(missing_movie_ids)) ## missing movies
print(len(total_missing), total, qs.count())

6392 57175 100004


In [8]:
links_df = pd.read_csv(LINKS_SAMLL_CSV)
links_df.head()

movieId  imdbId   tmdbId
0        1  114709    862.0
1        2  113497   8844.0
2        3  113228  15602.0
3        4  114885  31357.0
4        5  113041  11862.0

In [11]:
ms_df = links_df.copy()[links_df.movieId.isin(total_missing)]
ms_df.head()

movieId  imdbId   tmdbId
0        1  114709    862.0
3        4  114885  31357.0
6        7  114319  11860.0
7        8  112302  45325.0
8        9  114576   9091.0

In [14]:
ms_df.shape[0] == len(total_missing)

True

In [16]:
def enrich_imdb_col(val):
    val = str(val)
    if len(val) == 7:
        return f'tt{val}'
    elif len(val) == 6:
        return f'tt0{val}'
    elif len(val) == 5:
        return f'tt00{val}'
    return val

In [18]:
ms_df['tt'] = ms_df['imdbId'].apply(enrich_imdb_col)

In [19]:
ms_df.head()

movieId  imdbId   tmdbId         tt
0        1  114709    862.0  tt0114709
3        4  114885  31357.0  tt0114885
6        7  114319  11860.0  tt0114319
7        8  112302  45325.0  tt0112302
8        9  114576   9091.0  tt0114576

In [20]:
MOVIES_CSV = settings.DATA_DIR / 'movies_metadata.csv'
MOVIES_CSV.exists()

True

In [21]:
movies_cols = ['title', 'overview', 'release_date', 'imdb_id']
movies_df = pd.read_csv(MOVIES_CSV, usecols=movies_cols)
movies_df.head()

imdb_id                                           overview release_date  \
0  tt0114709  Led by Woody, Andy's toys live happily in his ...   1995-10-30   
1  tt0113497  When siblings Judy and Peter discover an encha...   1995-12-15   
2  tt0113228  A family wedding reignites the ancient feud be...   1995-12-22   
3  tt0114885  Cheated on, mistreated and stepped on, the wom...   1995-12-22   
4  tt0113041  Just when George Banks has recovered from his ...   1995-02-10   

                         title  
0                    Toy Story  
1                      Jumanji  
2             Grumpier Old Men  
3            Waiting to Exhale  
4  Father of the Bride Part II

In [23]:
missing_movies_df = ms_df.merge(movies_df, left_on='tt', right_on='imdb_id')
missing_movies_df.head()

movieId  imdbId   tmdbId         tt    imdb_id  \
0        1  114709    862.0  tt0114709  tt0114709   
1        4  114885  31357.0  tt0114885  tt0114885   
2        7  114319  11860.0  tt0114319  tt0114319   
3        8  112302  45325.0  tt0112302  tt0112302   
4        9  114576   9091.0  tt0114576  tt0114576   

                                            overview release_date  \
0  Led by Woody, Andy's toys live happily in his ...   1995-10-30   
1  Cheated on, mistreated and stepped on, the wom...   1995-12-22   
2  An ugly duckling having undergone a remarkable...   1995-12-15   
3  A mischievous young boy, Tom Sawyer, witnesses...   1995-12-22   
4  International action superstar Jean Claude Van...   1995-12-22   

               title  
0          Toy Story  
1  Waiting to Exhale  
2            Sabrina  
3       Tom and Huck  
4       Sudden Death

In [25]:
missing_movies_df['id'] = missing_movies_df['movieId']
missing_movies_df['id_alt'] = missing_movies_df['tmdbId'].apply(lambda x: str(int(x)))
missing_movies_df.head()

movieId  imdbId   tmdbId         tt    imdb_id  \
0        1  114709    862.0  tt0114709  tt0114709   
1        4  114885  31357.0  tt0114885  tt0114885   
2        7  114319  11860.0  tt0114319  tt0114319   
3        8  112302  45325.0  tt0112302  tt0112302   
4        9  114576   9091.0  tt0114576  tt0114576   

                                            overview release_date  \
0  Led by Woody, Andy's toys live happily in his ...   1995-10-30   
1  Cheated on, mistreated and stepped on, the wom...   1995-12-22   
2  An ugly duckling having undergone a remarkable...   1995-12-15   
3  A mischievous young boy, Tom Sawyer, witnesses...   1995-12-22   
4  International action superstar Jean Claude Van...   1995-12-22   

               title  id id_alt  
0          Toy Story   1    862  
1  Waiting to Exhale   4  31357  
2            Sabrina   7  11860  
3       Tom and Huck   8  45325  
4       Sudden Death   9   9091

In [27]:
final_df = missing_movies_df.copy()[['id', 'id_alt', 'title', ]]
final_df.head()

id id_alt              title
0   1    862          Toy Story
1   4  31357  Waiting to Exhale
2   7  11860            Sabrina
3   8  45325       Tom and Huck
4   9   9091       Sudden Death

In [29]:
alt_id_list = final_df['id_alt'].tolist()

6035

In [43]:
from django.forms.models import model_to_dict

In [44]:
movies_qs = Movie.objects.filter(id__in=alt_id_list)
movies_qs.count()
for obj in movies_qs:
    data = final_df.copy()[final_df['id_alt'] == str(obj.id)]
    if data.shape[0] == 1:
        og_model_data = model_to_dict(obj)
        update_data = data.to_dict('records')[0]
        if obj.title == update_data.get('title'):
            print(og_model_data)
            og_model_data['id'] = update_data['id']
            new_model_data = {**og_model_data}
            print(new_model_data)
            obj.delete()
            Movie.objects.create(**new_model_data)

{'id': 6, 'title': 'Judgment Night', 'overview': 'While racing to a boxing match, Frank, Mike, John and Rey get more than they bargained for. A wrong turn lands them directly in the path of Fallon, a vicious, wise-cracking drug lord. After accidentally witnessing Fallon murder a disloyal henchman, the four become his unwilling prey in a savage game of cat &amp; mouse as they are mercilessly stalked through the urban jungle in this taut suspense drama', 'release_date': datetime.date(1993, 10, 15), 'rating_last_updated': datetime.datetime(2023, 12, 12, 10, 19, 20, 564259, tzinfo=datetime.timezone.utc), 'rating_count': 104, 'rating_avg': Decimal('3.95')}
{'id': 479, 'title': 'Judgment Night', 'overview': 'While racing to a boxing match, Frank, Mike, John and Rey get more than they bargained for. A wrong turn lands them directly in the path of Fallon, a vicious, wise-cracking drug lord. After accidentally witnessing Fallon murder a disloyal henchman, the four become his unwilling prey in a

In [45]:
from ratings.tasks import task_update_movie_ratings
task_update_movie_ratings()

Rating update takes 0:00:15 seconds
